In [1]:
import torch
torch.cuda.is_available()

True

In [2]:
import argparse
import json
import os
import torch
from tqdm import tqdm
from plotly import graph_objects as go
from scipy.io import wavfile
import nemo.collections.asr as nemo_asr
from nemo.collections.asr.models import EncDecCTCModel
import argparse
import multiprocessing
import os
import re
from pathlib import Path
from typing import List

import regex
import scipy.io.wavfile as wav
from scripts_ctc.normalization_helpers import LATIN_TO_RU, RU_ABBREVIATIONS
from num2words import num2words

from nemo.collections import asr as nemo_asr

try:
    from nemo_text_processing.text_normalization.normalize import Normalizer

    NEMO_NORMALIZATION_AVAILABLE = True
except (ModuleNotFoundError, ImportError):
    NEMO_NORMALIZATION_AVAILABLE = False
    
from IPython.display import Audio
import json

import numpy as np
from scripts_ctc.utils import get_segments, listener_configurer, listener_process, worker_configurer, worker_process

import os
from pathlib import PosixPath
from typing import List, Tuple, Union

import ctc_segmentation as cs
import numpy as np

[NeMo W 2021-12-03 15:17:47 optimizers:46] Apex was not found. Using the lamb optimizer will error out.
[NeMo W 2021-12-03 15:18:04 nemo_logging:349] D:\Anaconda\lib\site-packages\pydub\utils.py:170: RuntimeWarning: Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work
      warn("Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work", RuntimeWarning)
    
################################################################################
### WARNING, path does not exist: KALDI_ROOT=/mnt/matylda5/iveselyk/Tools/kaldi-trunk
###          (please add 'export KALDI_ROOT=<your_path>' in your $HOME/.profile)
###          (or run as: KALDI_ROOT=<your_path> python <your_script>.py)
################################################################################

[NeMo W 2021-12-03 15:18:19 experimental:27] Module <class 'nemo.collections.asr.data.audio_to_text_dali.AudioToCharDALIDataset'> is experimental, not ready for production and is not fully supported. Us

In [3]:
from scripts_ctc.ctc_usage import CTCSegment

In [4]:
output_dir = 'test/crowd/'
segments_dir = output_dir+'/segments'
manifest = 'test/crowd/manifest.json'
window_len = 8000
no_parallel = True
sample_rate = 16000
model = '/workspace/models/QuartzNet15x5_golos.nemo'
debug = True

In [5]:
with open(manifest, 'r') as file:
    lines = json.load(file)

In [6]:
audio_files = [output_dir+line['audio_filepath'] for line in lines]
texts = [line['text'] for line in lines]
processed_texts = [[k.strip() for k in line['text'].split()] for line in lines]

In [7]:
audio_file = audio_files[0]
text = texts[0]

In [8]:
audio_file

'test/crowd/files/e632f7d39c15e7edfc665b91e6f2071f.wav'

In [9]:
analyzer = CTCSegment(model_path = 'QuartzNet15x5_golos.nemo')

[NeMo W 2021-12-03 15:18:36 modelPT:137] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: train/golos_and_mcv.jsonl
    sample_rate: 16000
    labels:
    - ' '
    - а
    - б
    - в
    - г
    - д
    - е
    - ж
    - з
    - и
    - й
    - к
    - л
    - м
    - н
    - о
    - п
    - р
    - с
    - т
    - у
    - ф
    - х
    - ц
    - ч
    - ш
    - щ
    - ъ
    - ы
    - ь
    - э
    - ю
    - я
    batch_size: 64
    trim_silence: false
    max_duration: 20.0
    min_duration: 0.1
    num_workers: 20
    shuffle: true
    is_tarred: false
    tarred_audio_filepaths: null
    tarred_shard_strategy: scatter
    parser: ru
    
[NeMo W 2021-12-03 15:18:36 modelPT:144] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a

[NeMo I 2021-12-03 15:18:36 features:252] PADDING: 16
[NeMo I 2021-12-03 15:18:36 features:269] STFT using torch
[NeMo I 2021-12-03 15:19:49 modelPT:434] Model EncDecCTCModel was successfully restored from QuartzNet15x5_golos.nemo.


In [11]:
with open(manifest, 'r') as file:
    lines = json.load(file)

In [12]:
lines[3616]

{'id': 'e717f5aa5eb14e3bf5d10b2641106033',
 'audio_filepath': 'files/e717f5aa5eb14e3bf5d10b2641106033.wav',
 'text': 'афина побег какого писателя с каторги готовили ишутинцы ',
 'duration': 6.74}

In [15]:
audio_file = 'test/crowd/files/e717f5aa5eb14e3bf5d10b2641106033.wav'
text = lines[3616]['text']

In [16]:
# audio_files = [output_dir+line['audio_filepath'] for line in lines]

In [17]:
# for num, audio_file in enumerate(audio_files):
#     if audio_file == 'test/crowd/files/e717f5aa5eb14e3bf5d10b2641106033.wav':
#         print(num)

In [21]:
analyzer.process_file(audio_file, text, output_dir, preprocess = 'chars')

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

{'audio_filepath': 'test/crowd//cut\\high_score_clips\\e717f5aa5eb14e3bf5d10b2641106033_0000.wav', 'duration': 0.2464375, 'text': 'а', 'score': -0.87}


'Reference text:       а'


--------------------------------------------------------------------------------------------------------------
{'audio_filepath': 'test/crowd//cut\\high_score_clips\\e717f5aa5eb14e3bf5d10b2641106033_0001.wav', 'duration': 0.066375, 'text': 'ф', 'score': -4.73}


'Reference text:       ф'

...

'Reference text:       ц'


--------------------------------------------------------------------------------------------------------------
{'audio_filepath': 'test/crowd//cut\\high_score_clips\\e717f5aa5eb14e3bf5d10b2641106033_0054.wav', 'duration': 0.0663125, 'text': 'ы', 'score': -4.23}


'Reference text:       ы'


--------------------------------------------------------------------------------------------------------------


([[2.06, 2.58, -0.8721977803351871, 'а'],
  [2.58, 2.72, -4.7291955053239505, 'ф'],
  [2.72, 2.8600000000000003, -6.428727686403704, 'и'],
  [2.8600000000000003, 3.0, -6.938333034504467, 'н'],
  [3.0, 3.3200000000000003, -2.1220159231493767, 'а'],
  [3.3200000000000003, 3.3200000000000003, 0, ' '],
  [3.3200000000000003, 3.8200000000000003, -0.006964019412056206, 'п'],
  [3.8200000000000003, 3.92, -7.754305541515322, 'о'],
  [3.92, 4.1, -3.7781716720272964, 'б'],
  [4.1, 4.220000000000001, -5.9849533434869215, 'е'],
  [4.220000000000001, 4.460000000000001, -3.7922279434184247, 'г'],
  [4.460000000000001, 4.460000000000001, 0, ' '],
  [4.460000000000001, 4.76, -0.004834656664309632, 'к'],
  [4.76, 4.88, -7.859356757296989, 'а'],
  [4.88, 5.04, -5.0437897224323915, 'к'],
  [5.04, 5.140000000000001, -6.650903165340253, 'о'],
  [5.140000000000001, 5.26, -4.624820768749025, 'г'],
  [5.26, 5.380000000000001, -6.962303678191347, 'о'],
  [5.380000000000001, 5.380000000000001, 0, ' '],
  [5.380

In [22]:
segm, segm_frames = analyzer.timit(audio_file, text, output_dir)

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

In [23]:
# analyzer.process_folder(manifest, output_dir)

In [24]:
analyzer.timit_folder(manifest, output_dir)

Has 9994 files
test/crowd/files/e632f7d39c15e7edfc665b91e6f2071f.wav


Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

test/crowd/files/5db5df8bb9e3b6660b2a04b34d4a355d.wav


Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

[NeMo W 2021-12-03 15:32:53 nemo_logging:349] D:\Anaconda\lib\site-packages\ctc_segmentation\ctc_segmentation.py:241: RuntimeWarning:
    
    Mean of empty slice.
    
    
[NeMo W 2021-12-03 15:32:53 nemo_logging:349] D:\Anaconda\lib\site-packages\numpy\core\_methods.py:189: RuntimeWarning:
    
    invalid value encountered in double_scalars
    
    


...

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

test/crowd/files/09ac1f9718c6da18380b4a01d92d2561.wav


Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

test/crowd/files/a083e695744a9191ebb7f8cc85925f9f.wav


Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]